In [15]:
from IPython.display import HTML

HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
<form action="javascript:code_toggle()"><input type="submit" value="Click here to toggle on/off the raw code."></form>''')

# Kaggle Animal Shelter Results

The following report gives the results from the Kaggle Animal Shelter Competition.

## Project Description

The goal of this project is to predict the outcome of animals as they leave a shelter in Austin, Texas.  The outcome for each animal is one of the following: Adoption, Died, Euthanasia, Return to Owner or Transfer. We are given a train set and test set.  The test set does not include outcome labels and is used for competition leaderboard scoring.  This analysis uses only the train set which has labels.


In [52]:
# Import modules

import pandas as pd
import numpy as np
import os
import sys
import random
import copy
import cPickle as pickle
import datetime

import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot
import colorlover as cl
import matplotlib.pyplot as plt 

src_dir = os.path.join(os.getcwd(), os.pardir)
sys.path.append(src_dir)

from sklearn.model_selection import ShuffleSplit
from scipy.stats import spearmanr
from scipy import stats
from sklearn import decomposition
from sklearn.preprocessing import StandardScaler
from scipy.stats import boxcox
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error

import src.plotting_methods as pm
#import imp
#pm = imp.load_source('pm', '/Volumes/Work/Projects/Kaggle_Animal_Shelter/src/plotting_methods.py')

init_notebook_mode(connected=True)

%reload_ext autoreload
%autoreload 2

import warnings
warnings.simplefilter("ignore", DeprecationWarning)

pd.options.display.float_format = '{:,.4f}'.format

In [7]:
# Load data

#raw_data_dir = 'C:\Users\Colleen\Documents\Kaggle_Animal_Shelter\data'
#raw_data_dir = '/Volumes/Work/Projects/Kaggle_Animal_Shelter/data'
raw_data_dir = "D:\Cary's Stuff\Documents\Colleen's Stuff\Kaggle_Animal_Shelter\data"

f = open(os.path.join(raw_data_dir, 'train.csv'), 'r')
train_data = pd.read_csv(f)
f.close()


## Data Exploration and Feature Engineering

The data set has the following size:

In [50]:
print 'Number of samples: ' + str(train_data.shape[0])
print 'Number of columns: ' + str(train_data.shape[1])

Number of samples: 26729
Number of columns: 10


The columns, their types and number of unique values are shown below, along with the first few rows of the data

In [54]:
df = pd.concat([train_data.dtypes, train_data.apply(lambda x: len(np.unique(x)))], 1)
df.columns = ['type', 'num_unique_vals']
df

type  num_unique_vals
AnimalID        object            26729
Name            object            14065
DateTime        object            22918
OutcomeType     object                5
OutcomeSubtype  object            13628
AnimalType      object                2
SexuponOutcome  object                6
AgeuponOutcome  object               62
Breed           object             1380
Color           object              366

In [55]:
train_data.head()

AnimalID     Name             DateTime      OutcomeType OutcomeSubtype  \
0  A671945  Hambone  2014-02-12 18:22:00  Return_to_owner            NaN   
1  A656520    Emily  2013-10-13 12:44:00       Euthanasia      Suffering   
2  A686464   Pearce  2015-01-31 12:28:00         Adoption         Foster   
3  A683430      NaN  2014-07-11 19:09:00         Transfer        Partner   
4  A667013      NaN  2013-11-15 12:52:00         Transfer        Partner   

  AnimalType SexuponOutcome AgeuponOutcome                        Breed  \
0        Dog  Neutered Male         1 year        Shetland Sheepdog Mix   
1        Cat  Spayed Female         1 year       Domestic Shorthair Mix   
2        Dog  Neutered Male        2 years                 Pit Bull Mix   
3        Cat    Intact Male        3 weeks       Domestic Shorthair Mix   
4        Dog  Neutered Male        2 years  Lhasa Apso/Miniature Poodle   

         Color  
0  Brown/White  
1  Cream Tabby  
2   Blue/White  
3   Blue Cream  
4          Tan

We can ignore 'AnimalID' since its just a unique identify for each animal. The 'OutcomeType' is our target variable.  The features appear to all be string types.

This is clearly a multi-class classification problem with mostly categorical variables. Some of these variables have large number of categories which we will need to reduce.  Also there are some missing values we need to deal with.

We will go through each variable and do some cleaning and transformations into usable features. We need to use the full data set in order to capture all the categories for each variable.  However, we'll do further exploration using only a training set

First we split the data into training and testing sets - we'll use cross-validation to optimize parameters so we only the two sets.

In [59]:
# Split data, we'll use a stratified sampling with proportions 80-20

from sklearn.model_selection import train_test_split

split_seed = 5

df = train_data.drop(['Name', 'OutcomeType'], 1).copy()

X_train, X_test, y_train, y_test = train_test_split(
    df, train_data['OutcomeType'], test_size=0.2, random_state=split_seed,
    stratify = train_data['OutcomeType'])

### DateTime

These are strings, so we convert them to datetime objects.  We print the first few values and plot the distribution of times.

In [60]:
X_train['DateTime'].head()

12467    2015-03-11 14:01:00
15506    2013-12-01 23:58:00
7251     2015-01-30 14:55:00
23360    2014-12-29 16:10:00
7993     2014-05-01 17:33:00
Name: DateTime, dtype: object

In [61]:
times = pd.Series([datetime.datetime.strptime(x, '%Y-%m-%d %H:%M:%S') for x in X_train['DateTime']], index = X_train.index)
#X_train.drop('DateTime', axis = 1, inplace = True)
X_train.loc[:, 'DateTime'] = pd.Series(times)

In [50]:
iplot([go.Histogram(x = X_train['DateTime'])])

There doesn't seem to be any outliers or weird values, and the date range agrees with what's given in the competition description. In addition there appears to be spikes in events in the summer, which we'll investigate later.

To investigate further, we'll plot the distribution for each outcome variable.

In [53]:
figs = [go.Figure(data = [go.Histogram(x = g, name = ind, histnorm='probability')], 
                  layout = go.Layout(title = ind)) for ind,g in X_train['DateTime'].groupby(y_train)]
fig = pm.subplot_helper_fig(3, 2, figs)
fig['layout'].update(height = 1000)
fig['layout'].update(title = 'Distribution of Date with Outcome')
iplot(fig)

1. For all outcomes except for return to owner, there is a peak in the summer of 2015 and a smaller peak in the summer of 2014
2. Return to owner is fairly evenly distributed, except for a small peak around fall 2016.
3. There's a small peak in adoption around xmas time in 2014 and 2015, which makes sense.
4. Euthanasia drops off significantly after summer 2015 - possible due to different policies on euthanizing unwanted animals.

Since we can't input dates directly into a model, we'll need to change this variable.

Next lets look at the same plots using month, weekday and year

In [54]:
figs = [go.Figure(data = [go.Histogram(x = [k.month for k in g], name = ind, histnorm='probability')], 
                  layout = go.Layout(title = ind)) for ind,g in X_train['DateTime'].groupby(y_train)]
fig = pm.subplot_helper_fig(3, 2, figs)
fig['layout'].update(height = 1000)
fig['layout'].update(title = 'Distribution of Month with Outcome')
iplot(fig)

In [56]:
figs = [go.Figure(data = [go.Histogram(x = [k.weekday() for k in g], name = ind, histnorm='probability')], 
                  layout = go.Layout(title = ind)) for ind,g in X_train['DateTime'].groupby(y_train)]
fig = pm.subplot_helper_fig(3, 2, figs)
fig['layout'].update(height = 1000)
fig['layout'].update(title = 'Distribution of Day of Week with Outcome')
iplot(fig)

In [57]:
figs = [go.Figure(data = [go.Histogram(x = [k.year for k in g], name = ind, histnorm='probability')], 
                  layout = go.Layout(title = ind)) for ind,g in X_train['DateTime'].groupby(y_train)]
fig = pm.subplot_helper_fig(3, 2, figs)
fig['layout'].update(height = 1000)
fig['layout'].update(title = 'Distribution of Year with Outcome')
iplot(fig)

In [ ]:
Judging by these plots, we can add the following features:
    1. Month
    2. Day of Week
    3. Year

### OutcomeType

This is the target variable. We print the counts for each level.

Right away we can see the target variable is unbalanced.  This means we shouldn't use accuracy when assessing models - we'll use F1 score and look at precision vs recall.

In [41]:
train_data['OutcomeType'].groupby(train_data['OutcomeType']).count().append(pd.Series({'nan': len(train_data['OutcomeType']) - train_data['OutcomeType'].count()}))

Adoption           10769
Died                 197
Euthanasia          1555
Return_to_owner     4786
Transfer            9422
nan                    0
dtype: int64

### OutcomeSubtype

This is the subtype of the outcome, further describing what happened to each animal.  We print the counts for each level.

In [40]:
train_data['OutcomeSubtype'].groupby(train_data['OutcomeSubtype']).count().append(pd.Series({'nan': len(train_data['OutcomeSubtype']) - train_data['OutcomeSubtype'].count()}))

Aggressive               320
At Vet                     4
Barn                       2
Behavior                  86
Court/Investigation        6
Enroute                    8
Foster                  1800
In Foster                 52
In Kennel                114
In Surgery                 3
Medical                   66
Offsite                  165
Partner                 7816
Rabies Risk               74
SCRP                    1599
Suffering               1002
nan                    13612
dtype: int64

Thre are many missing values and some categories with very few samples.  We may be able to merge some of these categories.  But we'll leave it for now. 

### AnimalType

This one is categorical and simple - cat or dog. The following are the counts. Its approximately an even split between the animals.

In [42]:
train_data['AnimalType'].groupby(train_data['AnimalType']).count().append(pd.Series({'nan': len(train_data['AnimalType']) - train_data['AnimalType'].count()}))

Cat    11134
Dog    15595
nan        0
dtype: int64

Plotting the distribution of animal type with outcome gives the following:

In [63]:
cnts = pd.crosstab(X_train['AnimalType'], y_train)
cnts = cnts.apply(lambda x: x/float(sum(x)), 1)
iplot(go.Figure(data = [go.Bar(x = cnts.columns, y = cnts.loc[x,:], name = x) for x in cnts.index],
               layout = go.Layout(title = 'Distribution of Animal Type with Outcome')))

1. About 40% of cats and 40% of dogs are adopted
2. A greater percentage of dogs are returned to owner than cats.  Possibly because cats are harder to find when they get lost and many are outdoor cats
3. A greater percentage of cats are transfered.

### SexuponOutcome

This one is also categorical, indicating spayed/neutered status and sex of the animal.  These are the counts.  

In [43]:
train_data['SexuponOutcome'].groupby(train_data['SexuponOutcome']).count().append(pd.Series({'nan': len(train_data['SexuponOutcome']) - train_data['SexuponOutcome'].count()}))

Intact Female    3511
Intact Male      3525
Neutered Male    9779
Spayed Female    8820
Unknown          1093
nan                 1
dtype: int64

We'll change the 'Unknown' values to just missing.  It also makes sense to split this into two variables: Sex and IsFixed since, intuitively, sex could affect the outcome of the animal: Some people may prefer one sex to another for adoption, and male and female animals are subject to different health problems.  Also the fixed status could affect outcome, such as people being less likely to adopt intact animals due to aggression.  However doing this would remove interaction effects between Sex and IsFixed, so we may add these effects back in later.

In [69]:
X_train.loc[:, 'Sex'] = pd.Series([int('Female' in x) if isinstance(x, str) else np.nan for x in X_train['SexuponOutcome']], index = X_train.index)
X_train.loc[:, 'IsFixed'] = pd.Series([int('Intact' not in x) if isinstance(x, str) else np.nan for x in X_train['SexuponOutcome']], index = X_train.index)

Looking at the distribution of each with the outcome gives the following:

In [70]:
cnts = pd.crosstab(X_train['Sex'], y_train)
cnts.index = ['Male', 'Female']
cnts = cnts.apply(lambda x: x/float(sum(x)), 1)
iplot(go.Figure(data = [go.Bar(x = cnts.columns, y = cnts.loc[x,:], name = x) for x in cnts.index],
               layout = go.Layout(title = 'Distribution of Sex with Outcome')))

In [71]:
cnts = pd.crosstab(X_train['IsFixed'], y_train)
cnts.index = ['Not Fixed', 'Fixed']
cnts = cnts.apply(lambda x: x/float(sum(x)), 1)
iplot(go.Figure(data = [go.Bar(x = cnts.columns, y = cnts.loc[x,:], name = x) for x in cnts.index],
               layout = go.Layout(title = 'Distribution of Fixed Status with Outcome')))

Sex doesn't appear to affect the outcome significantly on its own. However it appears that fixed animals are much more likely to be adopted, but non-fixed animals are much more likely to be transfered. (Possibly for fixing procedure)

Thus, we'll keep these variables since sex might interact with another variable and fixed status appears to be related to outcome.

### AgeuponOutcome 

These are the unique values:

In [8]:
np.unique(train_data['AgeuponOutcome'])

array([nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
       nan, nan, nan, nan, nan, '0 years', '1 day', '1 month', '1 week',
       '1 weeks', '1 year', '10 months', '10 years', '11 months',
       '11 years', '12 years', '13 years', '14 years', '15 years',
       '16 years', '17 years', '18 years', '19 years', '2 days',
       '2 months', '2 weeks', '2 years', '20 years', '3 days', '3 months',
       '3 weeks', '3 years', '4 days', '4 months', '4 weeks', '4 years',
       '5 days', '5 months', '5 weeks', '5 years', '6 days', '6 months',
       '6 years', '7 months', '7 years', '8 months', '8 years',
       '9 months', '9 years'], dtype=object)

Since age is typically nominal, we can convert these into numbers.  The smallest unit of measure here is days so we'll convert these all to days and plot the histogram.

In [73]:
def get_age(s):
    
    if (s == 'nan') or (isinstance(s, float) and np.isnan(s)):
        return s
    
    n = s.split(' ')
    num = int(n[0])
    time = n[1]
    if num == 0:
        return 0
    elif 'year' in time:
        return num * 365
    elif 'month' in time:
        return num * 30
    else:
        return num

In [76]:
X_train.loc[:,'AgeuponOutcome'] = pd.Series([get_age(s) for s in X_train['AgeuponOutcome']])

In [78]:
iplot([go.Histogram(x = X_train['AgeuponOutcome'])])

This data has an odd distribution - the smaller the age, the more resolution there is.  This makes sense since the age of young animals tend to be measures with high resolution (i.e days and weeks), where as the ages of older animals are typically in years.  In addtion, the age of many of these animals is likely estimated so naturally they'd be heavily binned. (e.g. 1 year, 5 years, 20 years)

We'll plot the distribution with the outcome.

In [87]:
iplot(go.Figure(data = [go.Histogram(x = g, name = ind, histnorm='probability') for ind,g in X_train['AgeuponOutcome'].groupby(y_train)],
               layout = go.Layout(xaxis = dict(range = [0, 5000]),
                                 title = 'Distribution of Age with Outcome')))

There doesn't appear to be a strong relation between age and outcome, which seems counterintuitive.  But perhaps this variable interacts with other variables.

## Breed

The number of breeds was very high, around 1300.  The following are the counts and unique values (for the full data set):

In [62]:
x = 'Breed'
cnts = train_data[x].groupby(train_data[x]).count().append(pd.Series({'nan': len(train_data[x]) - train_data[x].count()}))

In [68]:
cnts.sort_values()

nan                                                   0
Newfoundland/Queensland Heeler                        1
Newfoundland/Great Pyrenees                           1
Newfoundland/Border Collie                            1
Newfoundland/Australian Cattle Dog                    1
Chinese Crested/Chihuahua Longhair                    1
Chinese Crested/Papillon                              1
Munchkin Longhair Mix                                 1
Miniature Schnauzer/Whippet                           1
Chihuahua Shorthair/Smooth Fox Terrier                1
Chinese Sharpei/Airedale Terrier                      1
Chinese Sharpei/Basset Hound                          1
Miniature Schnauzer/West Highland                     1
Chinese Sharpei/Great Dane                            1
Miniature Schnauzer/Soft Coated Wheaten Terrier       1
Chinese Sharpei/Pit Bull                              1
Miniature Schnauzer/Shih Tzu                          1
Miniature Schnauzer/Scottish Terrier            

Further investigation shows that the breed names can have the following formats:
    
1. A single breed. E.g. Beagle
2. A combo of two breeds. E.g. Chihuahua Shorthair/Finnish Spitz
3. A combo of three breeds. E.g. Labrador Retriever/Black/Tan Hound
4. Some mix involving a breed. E.g. Pit Bull Mix (unsure if the given breed is the dominant one in the mix or based on some other identification)


Given the high number of categories, and many categories having only 1 member, we should compress these.  We'll turn this into multi-categories by splitting the given breed names into their components - single breeds and the mix identifier. Thus each animal will be assigned 1 to 3 categories of breeds.

E.g. Labrador Retriever/Black/Tan Hound will be assigned the following categories: Labrador Retriever, Black and Tan Hound

E.g. Pit Bull Mix is assigned: Pit Bull and Mix.

This method has the following effects:

1. Eliminates interaction effects between breeds. However, we can add those back in and in a more targeted fashion (i.e. only the interactions which improve classification)
2. Assumes that 'Mix' is a category in itself. We can investigate this effect later
3. Assumes that order of breed doesn't matter. (E.g. 'Black/Tan Hound is same as 'Tan Hound/Black') We can also investigate this.

For now we'll use this method and investigate in more detail later.

In [60]:
from itertools import chain
breeds = np.unique(list(chain.from_iterable([x.split('/') for x in train_data['Breed']])))
breed_cnts = dict([(x, sum([x in y for y in train_data['Breed']])) for x in breeds])

new_breeds = list(np.unique([x.split(' Mix')[0] for x in breeds]))
new_breeds.append('Mix')
new_breed_cnts = dict([(x, sum([x in y for y in train_data['Breed']])) for x in new_breeds])

We now have this number of breed categories:

In [61]:
len(new_breed_cnts)

226

In [90]:
def get_breed_cat(x):
    n = x.split('/')
    
    cats = []
    for y in n:
        n2 = y.split(' Mix')
        if len(n2) == 2:
            n2[1] = 'Mix'
        cats.extend(n2)
    return cats

In [88]:
def convert_multi_cat_dummy(vals, pref, sep):
    dummies = {}
    df = pd.DataFrame(vals)
    cols = df.columns
    dummies = pd.get_dummies(df[cols[0]], columns = [cols[0]], prefix_sep=sep, prefix=pref)
    
    if len(cols) > 1:
        for c in cols[1:]:
            new_dummies = pd.get_dummies(df[c], columns = [c], prefix_sep=sep, prefix=pref)
            for x in new_dummies.columns:
                try:
                    v = dummies[x].copy()
                    dummies[x] = v + new_dummies[x]
                except:
                    dummies[x] = new_dummies[x]
                    
    return dummies

In [92]:
breed_cats = [get_breed_cat(x) for x in train_data['Breed']]
breed_dummies = convert_multi_cat_dummy(breed_cats, '', '')
breed_dummies = breed_dummies.loc[X_train.index,:]
breed_cols = list(breed_dummies.columns)

After converting the categories into dummy variables, we plot the distributions with outcome for the cost common breeds:

In [94]:
cnts = breed_dummies.loc[:, breed_cols].sum()
cols = list(cnts[cnts >= 500].index)
figs = []
for c in cols:
    y = y_train.loc[breed_dummies[c] == 1]
    cnts = y.groupby(y).count()
    cnts = cnts / float(sum(cnts))
    figs.append(go.Figure(data = [go.Bar(x = cnts.index, y = cnts.values)],
                         layout = go.Layout(title = c)))
fig = pm.subplot_helper_fig(3,3, figs)
fig['layout'].update(height = 1000)
fig['layout'].update(title = 'Distribution of Most Common Breeds with Outcome')
iplot(fig)

We can see most of these breeds the majority of animals adopted.  However, the pitbulls had more euthanasia and returning to the owner. The domestic breeds (all cats) shows a large portion transfered. So there is definitely some relationships between breed and outcome, but they may depend on how breed interacts with animal type.

## Color

There are around 350 colors, which is less than the original number of breeds but we can still try to compress this. The counts from the original data set are the following:

In [9]:
x = 'Color'
cnts = train_data[x].groupby(train_data[x]).count().append(pd.Series({'nan': len(train_data[x]) - train_data[x].count()}))
cnts.sort_values()

nan                               0
Chocolate/Gold                    1
Chocolate/Gray                    1
Chocolate/Red Tick                1
Cream/Orange                      1
Cream/Red                         1
Cream/Red Tick                    1
Cream/Seal Point                  1
Fawn/Brown                        1
Chocolate/Cream                   1
Fawn/Brown Brindle                1
Fawn/Tricolor                     1
Gold/Black                        1
Gold/Buff                         1
Gold/Tan                          1
Gold/Yellow                       1
Gray Tabby/Black                  1
Gray/Red                          1
Liver Tick/White                  1
Yellow/Yellow                     1
Chocolate/Brown Merle             1
Chocolate/Brown Brindle           1
Calico/Orange Tabby               1
Brown Brindle/Blue Tick           1
Brown Brindle/Brown Brindle       1
Brown Brindle/Brown Merle         1
Brown Merle/Blue Merle            1
Brown Merle/Tan             

Similar to the breeds, colors can be one of the following formats:

1. A single color E.g. Blue
2. A combo of 2 colors E.g. White/Black

We can also turn these into multi-categories by splitting the color combos. E.g. White/Black is assigned White and Black.

This has the effect of removing the interactions between colors but we can add these back in. It also assumes the order doesn't matter.

In [12]:
from itertools import chain
colors = np.unique(list(chain.from_iterable([x.split('/') for x in train_data['Color']])))
color_cnts = dict([(x, sum([x in y for y in train_data['Color']])) for x in colors])
color_cats = [x.split('/') for x in train_data['Color']]

We now have this many color categories:

In [106]:
len(color_cnts)

57

In [95]:
color_dummies = convert_multi_cat_dummy(color_cats, 'cl', '_')
color_dummies = color_dummies.loc[X_train.index,:]
color_cols = list(color_dummies.columns)

In [ ]:
After converting the categories into dummy variables, we plot the distributions with outcome for the cost common breeds:

In [96]:
cnts = color_dummies.loc[:, color_cols].sum()
cols = list(cnts[cnts >= 692].index)
figs = []
for c in cols:
    y = y_train.loc[color_dummies[c] == 1]
    cnts = y.groupby(y).count()
    cnts = cnts / float(sum(cnts))
    figs.append(go.Figure(data = [go.Bar(x = cnts.index, y = cnts.values)],
                         layout = go.Layout(title = c)))
fig = pm.subplot_helper_fig(3,3, figs)
fig['layout'].update(height = 1000)
fig['layout'].update(title = 'Distribution of Most Common Colors with Outcome')
iplot(fig)

In [ ]:
There are also some relationships here.

This serves as a good first pass at data exploration and feature engineering.  So, we'll create a new dataframe based on this analysis and convert the all categorical variables to dummies. We also inpute a couple missing values in the Age, Sex and IsFixed columns with the most common values.

In [120]:
# Create features

all_feats = train_data.loc[:, ['AgeuponOutcome']]

all_feats.loc[:, 'AgeuponOutcome'] =  pd.Series([get_age(s) for s in train_data['AgeuponOutcome']])
all_feats.loc[:, 'AnimalType'] = train_data['AnimalType'].astype('category').cat.codes

all_feats.loc[:, 'Sex'] = pd.Series([int('Female' in x) if isinstance(x, str) else np.nan for x in train_data['SexuponOutcome']]).astype('category')
all_feats.loc[:, 'IsFixed'] = pd.Series([int('Intact' not in x) if isinstance(x, str) else np.nan for x in train_data['SexuponOutcome']]).astype('category')

all_feats.loc[:, 'OutcomeType'] = train_data['OutcomeType'].copy().astype('category')
all_feats.loc[:, 'OutcomeSubtype'] = train_data['OutcomeSubtype'].copy().astype('category')

times = [datetime.datetime.strptime(x, '%Y-%m-%d %H:%M:%S') for x in train_data['DateTime']]

month_dummies = pd.get_dummies(pd.Series([x.month for x in times]), 
                               columns=[], prefix = 'month', prefix_sep = '_')
weekday_dummies = pd.get_dummies(pd.Series([x.weekday() for x in times]), 
                               columns=[], prefix = 'weekday', prefix_sep = '_')
year_dummies = pd.get_dummies(pd.Series([x.year for x in times]), 
                               columns=[], prefix = 'year', prefix_sep = '_')

color_cats = [x.split('/') for x in train_data['Color']]
color_dummies = convert_multi_cat_dummy(color_cats, 'cl', '_')

breed_cats = [get_breed_cat(x) for x in train_data['Breed']]
breed_dummies = convert_multi_cat_dummy(breed_cats, '', '')

# Get column names for feature types
color_cols = list(color_dummies.columns)
breed_cols = list(breed_dummies.columns)
otsub_cols = list(all_feats['OutcomeSubtype'].cat.categories)
at_keys = dict(zip(range(2), train_data['AnimalType'].astype('category').cat.categories))

all_feats = pd.get_dummies(all_feats, columns=['OutcomeSubtype'], prefix = '', prefix_sep = '')
all_feats = pd.concat([all_feats, month_dummies, weekday_dummies, year_dummies, color_dummies, breed_dummies], 1)

In [121]:
# Inpute missing age values as most common value
from sklearn.preprocessing import Imputer

im = Imputer(strategy = 'most_frequent')
all_feats['AgeuponOutcome'] = Imputer(strategy = 'most_frequent').fit_transform(all_feats.loc[:, ['AgeuponOutcome']])
all_feats['Sex'] = Imputer(strategy = 'most_frequent').fit_transform(all_feats.loc[:, ['Sex']])
all_feats['IsFixed'] = Imputer(strategy = 'most_frequent').fit_transform(all_feats.loc[:, ['IsFixed']])

The final feature set has the following shape and first couple of rows:

In [122]:
all_feats.shape

(26729, 327)

In [123]:
all_feats.head()

AgeuponOutcome  AnimalType    Sex  IsFixed      OutcomeType  Aggressive  \
0        365.0000           1 0.0000   1.0000  Return_to_owner           0   
1        365.0000           0 1.0000   1.0000       Euthanasia           0   
2        730.0000           1 0.0000   1.0000         Adoption           0   
3          3.0000           0 0.0000   0.0000         Transfer           0   
4        730.0000           1 0.0000   1.0000         Transfer           0   

   At Vet  Barn  Behavior  Court/Investigation    ...      Whippet  \
0       0     0         0                    0    ...            0   
1       0     0         0                    0    ...            0   
2       0     0         0                    0    ...            0   
3       0     0         0                    0    ...            0   
4       0     0         0                    0    ...            0   

   Wire Hair Fox Terrier  Wirehaired Pointing Griffon  Yorkshire Terrier  \
0                      0                            0                  0   
1                      0                            0                  0   
2                      0                            0                  0   
3                      0                            0                  0   
4                      0                            0                  0   

   Borzoi  Mix  Rex  Spanish Water Dog  Tan Hound  Yorkshire  
0       0    1    0                  0          0          0  
1       0    1    0                  0          0          0  
2       0    1    0                  0          0          0  
3       0    1    0                  0          0          0  
4       0    0    0                  0          0          0  

[5 rows x 327 columns]

## Modeling

First we'll use a simple classification model - Logistic Regression - to get a baseline performance. 

To optimize the regularization parameter, we'll use cross validation with 3 folds on the training set.  We'll use 'ovr' for one-vs-rest classification of the multiple classes and f1 scoring since we have unbalanced classes.

In [132]:
X_train.shape

(21383, 327)

In [124]:
# Re-split the data with all the new features.
from sklearn.model_selection import train_test_split

split_seed = 5

df = all_feats.drop(['OutcomeType'], 1).copy()

X_train, X_test, y_train, y_test = train_test_split(
    df, all_feats['OutcomeType'], test_size=0.2, random_state=split_seed,
    stratify = all_feats['OutcomeType'])

In [128]:
# Scale

sc = StandardScaler()
scale_train_feats = pd.DataFrame(sc.fit_transform(X_train), columns = X_train.columns)
scale_test_feats = pd.DataFrame(sc.transform(X_test), columns = X_test.columns)

In [126]:
from sklearn.linear_model import LogisticRegressionCV

lr = LogisticRegressionCV(multi_class = 'ovr', scoring = 'f1')
lr.fit(scale_train_feats, y_train)

C:\Users\Ziilch\Anaconda2\lib\site-packages\sklearn\metrics\classification.py:1135: UndefinedMetricWarning:

F-score is ill-defined and being set to 0.0 due to no predicted samples.



LogisticRegressionCV(Cs=10, class_weight=None, cv=None, dual=False,
           fit_intercept=True, intercept_scaling=1.0, max_iter=100,
           multi_class='ovr', n_jobs=1, penalty='l2', random_state=None,
           refit=True, scoring='f1', solver='lbfgs', tol=0.0001, verbose=0)

These are the results from predicting with the test class. The F1 score is decent.  We can see that the Return_to_owner class had the lowest score, and Adoption was also lower than the others.

In [131]:
from sklearn.metrics import classification_report
print(classification_report(y_test, lr.predict(scale_test_feats), digits = 4))

                 precision    recall  f1-score   support

       Adoption     0.8111    0.9090    0.8573      2154
           Died     1.0000    0.9231    0.9600        39
     Euthanasia     1.0000    1.0000    1.0000       311
Return_to_owner     0.7190    0.5266    0.6080       957
       Transfer     1.0000    0.9995    0.9997      1885

    avg / total     0.8736    0.8779    0.8719      5346



To get an idea of overfitting, we look at the training scores:

In [132]:
print(classification_report(y_train, lr.predict(scale_train_feats), digits = 4))

                 precision    recall  f1-score   support

       Adoption     0.8113    0.9126    0.8590      8615
           Died     1.0000    0.9177    0.9571       158
     Euthanasia     1.0000    0.9992    0.9996      1244
Return_to_owner     0.7247    0.5247    0.6087      3829
       Transfer     1.0000    0.9993    0.9997      7537

    avg / total     0.8747    0.8788    0.8726     21383



The training and testing scores are very similar which suggests there is little overfitting. however the slightly low scores indicate some bias.

In [ ]:
We can also plot the ROC curves to look at the results:

In [135]:
from sklearn.metrics import roc_auc_score
from sklearn.metrics import roc_curve

cats = y_test.cat.categories
roc_figs = []
for i in range(len(cats)):
    probs = lr.predict_proba(scale_test_feats)
    labs = [int(x == cats[i]) for x in y_test]
    logit_roc_auc = roc_auc_score(labs, probs[:, i])
    fpr, tpr, thresholds = roc_curve(labs, probs[:, i])
    roc_figs.append(go.Figure(data = [go.Scatter(x = fpr, y = tpr, name='ROC curve'),
                                     go.Scatter(x = [0, 1.0], y = [0, 1.0], 
                                                name = 'Chance', marker = dict(color='black'), showlegend = i == 0)],
                             layout = go.Layout(title = cats[i])))
iplot(pm.subplot_helper_fig(3, 2, roc_figs))

Again you can see the issues with the Adoption and Return to owner classes.

## Future Work

We need to investigate these results more to increase the performance. Namely we can do the following:

1. Check the assumptions of the Logistic Regression
2. Conduct error analysis on the Adoption and Return_to_owner class: compare the correctly and incorrectly classified samples and look for patterns
3. Try a non-linear algorithm, such as Random Forest
4. Try adding interaction terms
5. Try a kernel method also for higher order interactions.